In [161]:
%config Completer.use_jedi = False
import spacy
import re
import numpy as np
import pylab as plt
import pandas as pd
import tqdm

Problems:
- Jalapeno vs. Jalapenos
- `str.find` found a match that `re.search` didn't
- Mislabeled data
- `Salt and pepper` vs `salt and freshly ground pepper`

Solution:
- Make unplural if plural if can't be found
- Try `str.find` if `re.search` doesn't work
- Skip I guess

Changes between models 1 and 2:

- Removed unnecessary words. Will be standard practice in the future when parsing strings
- Fix units
    - `(28-ounce can)` -> unit
    - `-ounce`
- Fix
    - `Salt and pepper` -> `Salt and freshly cracked pepper`

In [162]:
ingredients = pd.read_csv('../data/nyt-ingredients-snapshot-2015.csv')

In [163]:
patterns = ['\d+\s\d\/\d', '\d+\s(and)\s\d\/\d', '\d+\s(and)\s(a)\s(third|half|quarter|fourth)', '\d+']
a = ingredients.input.str.match(patterns[0])
b = ingredients.input.str.match(patterns[1])
c = ingredients.input.str.match(patterns[2])
d = ingredients.input.str.match(patterns[3])
np.nansum(np.any([a, b, c, d], axis=0))

154135

In [164]:
def preprocess(ingredients):
    strings = 0
    for i, row in enumerate(ingredients.itertuples()):
        try:
            string = reformat_string(row.input)
            strings += 1
            print (string, row.input)
            if i > 1000:
                break
            
        except:
            pass
        
    return strings

In [165]:
preprocess(ingredients)

1 1/4 1 1/4 cups cooked and pureed fresh butternut squash, or 1 10-ounce package frozen squash, defrosted
1 1 cup peeled and cooked fresh chestnuts (about 20), or 1 cup canned, unsweetened chestnuts
1 1 medium-size onion, peeled and chopped
2 2 stalks celery, chopped coarse
1 1/2 1 1/2 tablespoons vegetable oil
1/2 2 tablespoons unflavored gelatin, dissolved in 1/2 cup water
0 Salt
1 1 cup canned plum tomatoes with juice
6 6 cups veal or beef stock
1/3 1/3 cup Worcestershire sauce
1 1 tablespoon Louisiana hot sauce
1/2 1/2 teaspoon hot red pepper flakes
4 4 bay leaves
6 6 cloves garlic, crushed and chopped
2 2 carrots, peeled and diced
2 2 medium onions, diced
6 6 tablespoons butter
1 1 tablespoon Creole seasoning, or other seasonings of your choice
3 3 pounds beef brisket
1/2 1/2 cup fine dry bread crumbs
0 Freshly ground black pepper
12 12 oysters and their liquor
3 3 tablespoons minced scallions
1 1 tablespoon flour
6 6 ounces button mushrooms, thinly sliced then coarsely chopped
13

1000

Reformat the input data so that they all follow the same regex pattern. Right now the patterns are `1 3/4`, `1 and 3/4`, `1 and a third`. Make them conform to `1 3/4`

## Load Test/Train Data

In [160]:
def decimal_to_string(decimal):
    """
    """
    # Don't love this
    problem_fractions = {0.13: '1/8', 0.67: '2/3', 0.33: '1/3'}
    if decimal in problem_fractions:
        return problem_fractions.get(decimal)
    
    ratio = float(decimal).as_integer_ratio()
    return '/'.join(str(d) for d in ratio)

def string_to_decimal(string):
    """
    """
    numbers = string.split('/')
    return float(numbers[0]) / float(numbers[1])
    
def _process_and_colloquial(string):
    """
    """
    measurements = {'third': '1/3', 'half': '1/2', 'quarter': '1/4', 'fourth': '1/4'}
    splits = string.split(' and a ')
    return float(splits[0]) + measurements.get(splits[1], '')
    
def _process_and(string):
    """
    """
    splits = string.split(' and ')
    return float(splits[0]) + string_to_decimal(splits[1])

def _process(string):
    """
    """
    splits = string.split(' ')
    return float(splits[0]) + string_to_decimal(splits[1])

def string_to_float(string):
    """
    NOT GOOD NAMING
    """
    patterns = ['\d+\s(and)\s\d\/\d', '\d+\s\d\/\d']
    pattern_dict = {'\d+\s(and)\s\d\/\d': _process_and, '\d+\s\d\/\d': _process}
    
    for pattern in patterns:
        pt = re.compile(pattern)
        match = re.search(pt, string)
        if match:
            return pattern_dict[pattern](match.group())
        
    return 0

def reformat_string(string):
    """
    """
    patterns = ['\d+\s(and)\s\d\/\d', '\d+\s\d\/\d', '\d+\/\d+', '\d+']
    pattern_dict = {'\d+\s(and)\s\d\/\d': lambda x: float_to_string(_process_and(x)), 
                    '\d+\s\d\/\d': lambda x: x,
                    '\d+\/\d+': lambda x: x,
                    '\d+': lambda x: x}
    
    for pattern in patterns:
        pt = re.compile(pattern)
        match = re.search(pt, string)
        if match:
            return pattern_dict[pattern](match.group())
        
    return 0
    
            
def float_to_string(value):
    """
    """
    if value < 1:
        if (value - int(value)) < 0.001:
            return str(0)
        
        return decimal_to_string(value)
    
    if value == 1:
        return str(1)
    
    else:
        if (value - int(value)) < 0.001:
            return str(int(value))
        
        return '{} {}'.format(str(int(value)), decimal_to_string(round(value - int(value), 2)))

In [5]:
pattern = '[1-9]\s(and)\s(a)\s(quarter|half|third|fourth)'
bo = np.array(ingredients.input.str.match(pattern))
bo[pd.isna(bo)] = False
ingredients.iloc[bo].head(10)

index                                input         name   qty  \
118442  118442  1 and a half cups all-purpose flour        flour  1.00   
118811  118811         1 and a half cups white wine   white wine  1.50   
118813  118813       1 and a third cups blueberries  blueberries  1.33   
121844  121844   1 and a half teaspoons kosher salt  kosher salt  1.50   

        range_end      unit comment  
118442        0.0       cup     NaN  
118811        0.0       cup     NaN  
118813        0.0       cup     NaN  
121844        0.0  teaspoon     NaN

In [6]:
pattern = '(.*)[0-9]\.+[0-9]'
bo = np.array(ingredients.input.str.match(pattern))
bo[pd.isna(bo)] = False
ingredients.iloc[bo].head(10)

index                                              input  \
57600    57600  1 3.66-ounce can smoked oysters, drained, 1 te...   
108744  108744              1.5 liters dry red wine, about 6 cups   
114976  114976                    1 (15.5-ounce) can coconut milk   
115509  115509  0.75 pound squid, in 0.5-inch rings, plus tent...   
115624  115624  1 can chickpeas, drained and rinsed, or 1.5 cu...   
116278  116278  1 cup crustless day-old French bread, in 0.5-i...   
132533  132533                 1/4 teaspoon/1.5 grams baking soda   
152925  152925  1.75 liters of Everclear, or other strong or o...   
152937  152937  1.75 liters of Everclear, or other strong or o...   
160987  160987                      3.5 grams (1/2 teaspoon) salt   

                                                    name   qty  range_end  \
57600                                            oysters  3.66        0.0   
108744                        dry red wine, about 6 cups  1.50        0.0   
114976                     (15.5-ounce) can coconut milk  1.00        0.0   
115509                                             squid  0.75        0.0   
115624                                         chickpeas  1.00        0.0   
116278  crustless day-old French bread in 0.5 inch cubes  1.00        0.0   
132533                                       baking soda  0.25        0.0   
152925                                         Everclear  1.75        0.0   
152937                                         Everclear  1.75        0.0   
160987                                              salt  3.50        0.0   

            unit                                            comment  
57600      ounce  1 3.66-ounce can smoked, drained, 1of the oil ...  
108744     liter                                                NaN  
114976       NaN                                                NaN  
115509     pound                                                NaN  
115624       NaN                                                NaN  
116278       cup                                                NaN  
132533  teaspoon                                         /1.5 grams  
152925     liter                                                NaN  
152937     liter                                                NaN  
160987      gram                                                NaN

These look really poorly labeled. I feel like maybe I should cut them out of the training set. Considering there's only 27 of them, I feel like that wouldn't be a terrible thing to do. I'm going to need to handle this format eventually but maybe now isn't the best time.

In [7]:
pattern = '[1-9]/[1-9]'
bo = np.array(ingredients.input.str.match(pattern))
bo[pd.isna(bo)] = False
ingredients.iloc[bo].head(10)

index                                              input  \
10     10                       1/3 cup Worcestershire sauce   
12     12                 1/2 teaspoon hot red pepper flakes   
20     20                      1/2 cup fine dry bread crumbs   
31     31                       1/4 teaspoon vanilla extract   
35     35                                  1/4 teaspoon salt   
36     36                                      1/4 cup sugar   
45     45                 1/2 teaspoon hot red pepper flakes   
52     52  3/4 pound shiitake mushrooms, stemmed and quar...   
56     56                       1/8 teaspoon ground cinnamon   
61     61                                1/4 cup heavy cream   

                     name   qty  range_end        unit                comment  
10   Worcestershire sauce  0.33        0.0         cup                    NaN  
12  hot red pepper flakes  0.50        0.0    teaspoon                    NaN  
20           bread crumbs  0.50        0.0         cup               fine dry  
31        vanilla extract  0.25        0.0    teaspoon                    NaN  
35                   salt  0.25        0.0    teaspoon                    NaN  
36                  sugar  0.25        0.0         cup                    NaN  
45  hot red pepper flakes  0.50        0.0    teaspoon                    NaN  
52     shiitake mushrooms  0.75        0.0  tablespoon  stemmed and quartered  
56               cinnamon  0.13        0.0    teaspoon                 ground  
61            heavy cream  0.25        0.0         cup                    NaN

What string patterns do I need to deal with in the input for quantity:
- `1.5`
- `1 and a half`
- `1 and 1/2`
- `3/2`

## Reformat Training Data

Clean NYT Data:
- Search for the unit. Should be pretty straightfoward

In [16]:
def cleandata(ingredients):
    """
    """
    data = []
    for i, row in enumerate(ingredients.itertuples()):
        entry = {'entities': []}
        if pd.isna(row.input) or i in [52, 54, 184, 253, 274]:
            continue
            
        try:
            if not pd.isna(row.unit):
                unit = re.search(row.unit, row.input, re.IGNORECASE)
                entry['entities'].append((*unit.span(), 'UNIT'))

            """
            if not pd.isna(row.qty):
                print ('b')
                qty = re.search(str(int(row.qty)), row.input)

                if qty:
                    entry['entities'].append((*qty.span(), 'QUANTITY'))

                else:
                    entry['entities'].append((*string_to_float(row.input), 'QUANTITY'))
            """
            if not pd.isna(row.name):
                name = re.search(row.name, row.input, re.IGNORECASE)
                entry['entities'].append((*name.span(), 'PRODUCT'))

            data.append((row.input, entry))
            
        except Exception as e:
            print (e)
            print (i)
            print ('Input', row.input)
            print ('Unit', row.unit)
            print ('Name', row.name)
            print (pd.isna(row.unit))
            print (unit, name)
            break
    
    return data

In [31]:
def cleandata_debug_unit(ingredients):
    """
    """
    rows = []
    for i, row in enumerate(ingredients.itertuples()):
        entry = {'entities': []}
        if pd.isna(row.input):
            continue
            
        try:
            if not pd.isna(row.unit):
                unit = re.search(row.unit, row.input, re.IGNORECASE)
                entry['entities'].append((*unit.span(), 'UNIT'))
            
        except Exception as e:
            rows.append((i, e, row))
    
    return rows

def cleandata_debug_name(ingredients):
    """
    """
    rows = []
    for i, row in enumerate(ingredients.itertuples()):
        entry = {'entities': []}
        if pd.isna(row.input):
            continue
            
        try:
            if not pd.isna(row.name):
                name = re.search(row.name, row.input, re.IGNORECASE)
                entry['entities'].append((*name.span(), 'PRODUCT'))
            
        except Exception as e:
            rows.append((i, e, row))
    
    return rows

def cleandata_debug_qty(ingredients):
    """
    """
    rows = []
    for i, row in enumerate(ingredients.itertuples()):
        entry = {'entities': []}
        if pd.isna(row.input):
            continue
            
        try:
            if not pd.isna(row.qty):
                value = float_to_string(row.qty)
                #qty = re.search(value, row.input)
                #entry['entities'].append((*qty.span(), 'QUANTITY'))
            
        except Exception as e:
            rows.append((i, e, row))
    
    return rows

In [103]:
ingredients.iloc[3432]

index                    3432
input        1 1/4 cups flour
name                    flour
qty                      1.25
range_end                 0.0
unit                      cup
comment                   NaN
Name: 3432, dtype: object

In [100]:
for i, row in enumerate(ingredients.itertuples()):
    if not pd.isna(row.qty):
        print (i, row.qty, float_to_string(row.qty))

0 1.25 1 1/4
1 1.0 1
2 1.0 1
3 2.0 2
4 1.5 1 1/2
5 0.5 1/2
6 2.0 2
7 0.0 0
8 1.0 1
9 6.0 6
10 0.33 1/3
11 1.0 1
12 0.5 1/2
13 4.0 4
14 6.0 6
15 2.0 2
16 2.0 2
17 6.0 6
18 1.0 1
19 3.0 3
20 0.5 1/2
21 0.0 0
22 12.0 12
23 3.0 3
24 1.0 1
25 6.0 6
26 13.0 13
27 4.0 4
28 1.0 1
29 0.0 0
30 0.0 0
31 0.25 1/4
32 2.0 2
33 1.0 1
34 2.0 2
35 0.25 1/4
36 0.25 1/4
37 6.0 6
38 2.0 2
39 0.0 0
40 0.0 0
41 0.0 0
42 2.0 2
43 0.0 0
44 2.0 2
45 0.5 1/2
46 3.0 3
47 5.0 5
48 2.0 2
49 5.0 5
50 0.0 0
51 3.0 3
52 0.75 3/4
53 2.0 2
54 1.0 1
55 2.0 2
56 0.13 1/8
57 1.0 1
58 3.0 3
59 1.0 1
60 0.0 0
61 0.25 1/4
62 2.5 2 1/2
63 4.0 4
64 1.5 1 1/2
65 3.0 3
66 1.0 1
67 2.0 2
68 1.0 1
69 2.0 2
70 0.5 1/2
71 0.5 1/2
72 2.0 2
73 1.0 1
74 1.0 1
75 12.0 12
76 1.5 1 1/2
77 3.0 3
78 3.0 3
79 3.0 3
80 0.75 3/4
81 3.0 3
82 6.0 6
83 3.0 3
84 3.0 3
85 1.0 1
86 9.0 9
87 2.0 2
88 3.0 3
89 18.0 18
90 1.0 1
91 1.0 1
92 1.25 1 1/4
93 1.0 1
94 3.0 3
95 0.5 1/2
96 0.75 3/4
97 0.0 0
98 5.0 5
99 4.0 4
100 0.25 1/4
101 1.0 1
102 1.0 1
10

1280 1.0 1
1281 0.33 1/3
1282 0.0 0
1283 1.0 1
1284 4.0 4
1285 2.0 2
1286 1.0 1
1287 1.0 1
1288 2.0 2
1289 1.0 1
1290 0.5 1/2
1291 4.0 4
1292 0.75 3/4
1293 0.5 1/2
1294 1.0 1
1295 1.0 1
1296 4.0 4
1297 2.0 2
1298 1.0 1
1299 1.0 1
1300 0.0 0
1301 4.0 4
1302 3.0 3
1303 0.0 0
1304 1.0 1
1305 1.0 1
1306 1.0 1
1307 0.0 0
1308 3.0 3
1309 0.5 1/2
1310 0.75 3/4
1311 4.0 4
1312 0.75 3/4
1313 0.0 0
1314 0.25 1/4
1315 0.25 1/4
1316 1.0 1
1317 4.0 4
1318 1.0 1
1319 4.0 4
1320 1.0 1
1321 1.25 1 1/4
1322 0.0 0
1323 2.0 2
1324 6.0 6
1325 1.0 1
1326 5.0 5
1327 0.0 0
1328 0.0 0
1329 0.0 0
1330 1.0 1
1331 2.0 2
1332 8.0 8
1333 4.0 4
1334 0.25 1/4
1335 0.5 1/2
1336 2.5 2 1/2
1337 0.5 1/2
1338 0.25 1/4
1339 0.5 1/2
1340 2.0 2
1341 3.0 3
1342 3.0 3
1343 1.0 1
1344 1.0 1
1345 1.0 1
1346 1.0 1
1347 2.0 2
1348 2.0 2
1349 2.0 2
1350 1.0 1
1351 0.25 1/4
1352 0.5 1/2
1353 4.0 4
1354 2.0 2
1355 3.0 3
1356 0.25 1/4
1357 0.5 1/2
1358 1.5 1 1/2
1359 10.0 10
1360 2.0 2
1361 0.75 3/4
1362 0.5 1/2
1363 0.25 1/4
1364 4.

2484 1.0 1
2485 0.75 3/4
2486 1.0 1
2487 3.0 3
2488 0.0 0
2489 2.0 2
2490 1.0 1
2491 4.0 4
2492 0.25 1/4
2493 0.5 1/2
2494 0.5 1/2
2495 0.0 0
2496 0.5 1/2
2497 1.0 1
2498 3.0 3
2499 3.0 3
2500 6.0 6
2501 1.5 1 1/2
2502 1.0 1
2503 2.0 2
2504 3.0 3
2505 2.0 2
2506 0.0 0
2507 1.0 1
2508 3.0 3
2509 1.0 1
2510 1.5 1 1/2
2511 1.0 1
2512 1.0 1
2513 3.0 3
2514 1.0 1
2515 0.5 1/2
2516 1.5 1 1/2
2517 1.0 1
2518 2.0 2
2519 0.0 0
2520 1.0 1
2521 0.25 1/4
2522 3.0 3
2523 0.33 1/3
2524 0.25 1/4
2525 4.0 4
2526 2.0 2
2527 2.0 2
2528 0.25 1/4
2529 1.0 1
2530 0.0 0
2531 24.0 24
2532 1.0 1
2533 0.33 1/3
2534 0.33 1/3
2535 2.0 2
2536 4.0 4
2537 2.0 2
2538 1.0 1
2539 0.25 1/4
2540 0.5 1/2
2541 1.0 1
2542 2.0 2
2543 0.0 0
2544 2.0 2
2545 0.5 1/2
2546 6.0 6
2547 0.33 1/3
2548 0.0 0
2549 1.0 1
2550 0.0 0
2551 1.0 1
2552 1.0 1
2553 3.0 3
2554 24.0 24
2555 4.0 4
2556 0.5 1/2
2557 0.5 1/2
2558 2.0 2
2559 5.5 5 1/2
2560 1.0 1
2561 7.0 7
2562 0.0 0
2563 1.0 1
2564 24.0 24
2565 0.25 1/4
2566 0.5 1/2
2567 0.25 1/4


KeyboardInterrupt: 

In [71]:
float_to_string(3)

'3'

The search I'm doing may not be as reliable as I think it is

In [12]:
abc = ingredients.loc[184]

In [13]:
abc['input'].find(abc['name'])

7

In [14]:
re.search(abc['name'], abc['input'])

### Debug the Clean

In [18]:
_ = cleandata(ingredients)

'NoneType' object has no attribute 'span'
332
Input Salt and freshly ground black pepper
Unit nan
Name Salt and black pepper
True
<re.Match object; span=(2, 6), match='pint'> None


In [34]:
name_rows = cleandata_debug_name(ingredients)

In [35]:
unit_rows = cleandata_debug_unit(ingredients)

In [36]:
qty_rows = cleandata_debug_qty(ingredients)

In [70]:
ingredients.shape

(179207, 7)

In [37]:
len(name_rows), len(unit_rows), len(qty_rows)

(6189, 680, 59278)

In [29]:
# I don't think I'm going to fix this because I don't want to
# Leaves is the problem
for _, _, row in unit_rows:
    print (row)

Pandas(Index=2285, index=2285, input='Polenta (<a href="http://cooking.nytimes.com/recipes/1657-polenta">see recipe</a>)', name='Polenta', qty=1.5, range_end=0.0, unit='cup', comment='see recipe')
Pandas(Index=2590, index=2590, input='Leaves from 3 inner stalks celery', name='Leaves from 3 inner celery stalks', qty=0.0, range_end=0.0, unit='leaf', comment=nan)
Pandas(Index=2918, index=2918, input='4 branches fresh thyme', name='thyme', qty=4.0, range_end=0.0, unit='sprig', comment='fresh')
Pandas(Index=3332, index=3332, input='3 tablespons chopped fresh coriander', name='coriander', qty=3.0, range_end=0.0, unit='tablespoon', comment='chopped fresh')
Pandas(Index=3551, index=3551, input='1/4 cup plus 2 tablespoons sugar', name='sugar', qty=6.0, range_end=0.0, unit='teaspoon', comment=nan)
Pandas(Index=3997, index=3997, input='3 tablespooons melted unsalted butter', name='unsalted butter', qty=3.0, range_end=0.0, unit='tablespoon', comment='melted')
Pandas(Index=5209, index=5209, input='

In [26]:
for _, _, row in qty_rows:
    print (row)

Pandas(Index=7, index=7, input='Salt', name='Salt', qty=0.0, range_end=0.0, unit=nan, comment=nan)
Pandas(Index=10, index=10, input='1/3 cup Worcestershire sauce', name='Worcestershire sauce', qty=0.33, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=12, index=12, input='1/2 teaspoon hot red pepper flakes', name='hot red pepper flakes', qty=0.5, range_end=0.0, unit='teaspoon', comment=nan)
Pandas(Index=20, index=20, input='1/2 cup fine dry bread crumbs', name='bread crumbs', qty=0.5, range_end=0.0, unit='cup', comment='fine dry')
Pandas(Index=21, index=21, input='Freshly ground black pepper', name='black pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground')
Pandas(Index=29, index=29, input='Salt', name='Salt', qty=0.0, range_end=0.0, unit=nan, comment=nan)
Pandas(Index=30, index=30, input="Confectioners' sugar", name="Confectioners' sugar", qty=0.0, range_end=0.0, unit=nan, comment=nan)
Pandas(Index=31, index=31, input='1/4 teaspoon vanilla extract', name='vanilla e

Pandas(Index=5724, index=5724, input='1 tablespoon plus 1/3 cup dry white wine', name='dry white wine', qty=6.33, range_end=0.0, unit='tablespoon', comment=nan)
Pandas(Index=5725, index=5725, input='Freshly ground pepper to taste', name='pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground to taste')
Pandas(Index=5726, index=5726, input='Salt to taste if desired', name='Salt', qty=0.0, range_end=0.0, unit=nan, comment='to taste if desired')
Pandas(Index=5727, index=5727, input='Butter for greasing a pan', name='Butter', qty=0.0, range_end=0.0, unit=nan, comment='for greasing a pan')
Pandas(Index=5729, index=5729, input='Cayenne pepper', name='cayenne pepper', qty=0.0, range_end=0.0, unit=nan, comment=nan)
Pandas(Index=5732, index=5732, input='Freshly grated nutmeg', name='nutmeg', qty=0.0, range_end=0.0, unit=nan, comment='Freshly grated')
Pandas(Index=5733, index=5733, input='Coarse salt and freshly ground pepper', name='salt and pepper', qty=0.0, range_end=0.0, unit=nan

Pandas(Index=11584, index=11584, input='1/2 cup grated Parmesan cheese', name='Parmesan cheese', qty=0.5, range_end=0.0, unit='cup', comment='grated')
Pandas(Index=11586, index=11586, input='1/4 cup chopped flat-leaf parsley', name='parsley', qty=0.25, range_end=0.0, unit='cup', comment='chopped flat-leaf')
Pandas(Index=11590, index=11590, input='1/2 cup stellini (tiny star pasta)', name='stellini', qty=0.5, range_end=0.0, unit='cup', comment='tiny star pasta')
Pandas(Index=11599, index=11599, input='Salt and freshly ground black pepper', name='Salt and black pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=11601, index=11601, input='Red pepper flakes (optional)', name='Red pepper flakes', qty=0.0, range_end=0.0, unit=nan, comment='optional')
Pandas(Index=11602, index=11602, input='Sesame seeds', name='Sesame seeds', qty=0.0, range_end=0.0, unit=nan, comment=nan)
Pandas(Index=11606, index=11606, input='1/3 cup chopped salted peanuts', name='peanuts', qt

Pandas(Index=17762, index=17762, input='1/4 cup flour', name='flour', qty=0.25, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=17765, index=17765, input='1/2 teaspoon salt', name='salt', qty=0.5, range_end=0.0, unit='teaspoon', comment=nan)
Pandas(Index=17766, index=17766, input='1/4 teaspoon freshly ground black pepper', name='black pepper', qty=0.25, range_end=0.0, unit='teaspoon', comment='freshly ground')
Pandas(Index=17776, index=17776, input='1/2 cup brown sugar', name='brown sugar', qty=0.5, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=17777, index=17777, input='1/2 cup white sugar', name='white sugar', qty=0.5, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=17778, index=17778, input='Butterscotch sauce (see recipe)', name='Butterscotch sauce', qty=0.0, range_end=0.0, unit=nan, comment='see recipe')
Pandas(Index=17784, index=17784, input='2/3 cup firmly packed brown sugar', name='brown sugar', qty=0.67, range_end=0.0, unit='cup', comment='firmly packed')
Pand

Pandas(Index=24020, index=24020, input='1/4 cup grated ginger', name='ginger', qty=0.25, range_end=0.0, unit='cup', comment='grated')
Pandas(Index=24021, index=24021, input='3/4 cup minced parsley leaves', name='parsley leaves', qty=0.75, range_end=0.0, unit='cup', comment='minced')
Pandas(Index=24022, index=24022, input='1/4 cup minced coriander leaves', name='coriander leaves', qty=0.25, range_end=0.0, unit='cup', comment='minced')
Pandas(Index=24026, index=24026, input='1/2 teaspoon salt', name='salt', qty=0.5, range_end=0.0, unit='teaspoon', comment=nan)
Pandas(Index=24035, index=24035, input='1/2 teaspoon cardamom seeds', name='cardamom seeds', qty=0.5, range_end=0.0, unit='teaspoon', comment=nan)
Pandas(Index=24036, index=24036, input='1/2 teaspoon ground cinnamon', name='cinnamon', qty=0.5, range_end=0.0, unit='teaspoon', comment='ground')
Pandas(Index=24040, index=24040, input='1/2 teaspoon coriander seeds', name='coriander seeds', qty=0.5, range_end=0.0, unit='teaspoon', comme

Pandas(Index=30541, index=30541, input='1/2 bunch of thyme', name='thyme', qty=0.5, range_end=0.0, unit='bunch', comment=nan)
Pandas(Index=30543, index=30543, input='Freshly ground black pepper', name='black pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground')
Pandas(Index=30545, index=30545, input='1/2 cup breadcrumbs', name='breadcrumbs', qty=0.5, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=30546, index=30546, input='Salt', name='Salt', qty=0.0, range_end=0.0, unit=nan, comment=nan)
Pandas(Index=30552, index=30552, input='Salt and freshly ground black pepper', name='Salt and black pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=30557, index=30557, input='Salt and freshly ground black pepper', name='Salt and black pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=30559, index=30559, input='1/4 cup plus 1 tablespoon extra-virgin olive oil', name='olive oil', qty=5.0, range_end=0.0, unit='tablespo

Pandas(Index=35375, index=35375, input='1/2 cup pure maple syrup', name='maple syrup', qty=0.5, range_end=0.0, unit='cup', comment='pure')
Pandas(Index=35377, index=35377, input='1/4 cup canned chipotle peppers and sauce', name='chipotle peppers and sauce', qty=0.25, range_end=0.0, unit='cup', comment='canned,')
Pandas(Index=35382, index=35382, input='Sea salt', name='salt', qty=0.0, range_end=0.0, unit=nan, comment='Sea')
Pandas(Index=35386, index=35386, input='1/2 cup cold unsalted butter, cut into small pieces', name='unsalted butter', qty=0.5, range_end=0.0, unit='cup', comment='cold, cut into small pieces')
Pandas(Index=35387, index=35387, input='1/2 teaspoon kosher salt', name='salt', qty=0.5, range_end=0.0, unit='teaspoon', comment='kosher')
Pandas(Index=35394, index=35394, input='Pinch salt', name='salt', qty=1.0, range_end=0.0, unit='pinch', comment=nan)
Pandas(Index=35396, index=35396, input='Freshly ground pepper to taste', name='pepper', qty=0.0, range_end=0.0, unit=nan, co

Pandas(Index=41610, index=41610, input='1/2 teaspoon grated lemon rind', name='lemon rind', qty=0.5, range_end=0.0, unit='teaspoon', comment='grated')
Pandas(Index=41614, index=41614, input='Freshly ground pepper to taste', name='pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground to taste')
Pandas(Index=41630, index=41630, input='Freshly ground pepper to taste', name='pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground to taste')
Pandas(Index=41631, index=41631, input='1/2 cup chicken broth, homemade or low-sodium canned', name='chicken broth', qty=0.5, range_end=0.0, unit='cup', comment='homemade or low-sodium canned')
Pandas(Index=41632, index=41632, input='1/4 cup heavy cream', name='heavy cream', qty=0.25, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=41633, index=41633, input='1/3 cup grated taleggio', name='taleggio', qty=0.33, range_end=0.0, unit='cup', comment='grated')
Pandas(Index=41637, index=41637, input='Freshly ground pepper to taste'

Pandas(Index=47946, index=47946, input='6 4-ounce brook trout fillets', name='trout fillets', qty=24.0, range_end=0.0, unit='ounce', comment='6 4-ounce brook')
Pandas(Index=47947, index=47947, input='Freshly ground pepper to taste', name='pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground to taste')
Pandas(Index=47951, index=47951, input='1/2 cup heavy cream', name='heavy cream', qty=0.5, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=47952, index=47952, input='1/2 cup skim-milk ricotta', name='skim-milk ricotta', qty=0.5, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=47955, index=47955, input='1/4 cup water', name='water', qty=0.25, range_end=0.0, unit='cup', comment=nan)
Pandas(Index=47957, index=47957, input='Freshly ground pepper to taste', name='pepper', qty=0.0, range_end=0.0, unit=nan, comment='Freshly ground to taste')
Pandas(Index=47962, index=47962, input='1/4 cup water', name='water', qty=0.25, range_end=0.0, unit='cup', comment=nan)
Pandas(Index

KeyboardInterrupt: 

In [30]:
for _, _, row in name_rows:
    print (row)

Pandas(Index=332, index=332, input='Salt and freshly ground black pepper', name='Salt and black pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=347, index=347, input='Salt and freshly ground black pepper', name='Salt and black pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=362, index=362, input='Salt and freshly ground pepper', name='Salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=384, index=384, input='Sea salt and freshly ground black pepper', name='Sea salt and black pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground')
Pandas(Index=387, index=387, input='8 ounces stale Italian or sourdough bread, torn into 1-inch pieces', name='stale bread', qty=8.0, range_end=0.0, unit='ounce', comment='Italian or sourdough, torn into 1-inch pieces')
Pandas(Index=397, index=397, input='Salt and freshly ground black pepper', name='Salt and black pepper', qty=0.0, range_end=

Pandas(Index=52514, index=52514, input='Coarse salt and freshly ground pepper to taste', name='salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='Coarse freshly ground to taste')
Pandas(Index=52534, index=52534, input='Salt and freshly ground pepper to taste', name='Salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground to taste')
Pandas(Index=52543, index=52543, input='Salt and freshly ground pepper to taste', name='Salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground to taste')
Pandas(Index=52587, index=52587, input='4 garlic cloves, crushed', name='garlic, crushed', qty=4.0, range_end=0.0, unit='clove', comment=nan)
Pandas(Index=52648, index=52648, input='2 cups cooked fresh fava or white beans', name='cooked fresh fava beans', qty=2.0, range_end=0.0, unit='cup', comment='or white beans')
Pandas(Index=52662, index=52662, input='2 racks of lamb, trimmed and Frenched (ask your butcher to do this), trimmings reserved', name='racks o

Pandas(Index=109239, index=109239, input='Salt and freshly ground pepper to taste', name='Salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground to taste')
Pandas(Index=109248, index=109248, input='Coarse salt and freshly ground pepper to taste', name='salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='Coarse freshly ground to taste')
Pandas(Index=109265, index=109265, input='2 red and 2 yellow bell peppers, roasted, peeled, cored and cut into thin strips', name='red bell peppers', qty=2.0, range_end=0.0, unit=nan, comment='roasted, peeled, cored and cut into thin strips')
Pandas(Index=109379, index=109379, input='Salt and freshly ground pepper to taste', name='Salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground to taste')
Pandas(Index=109383, index=109383, input='Salt and freshly ground pepper to taste', name='Salt and pepper', qty=0.0, range_end=0.0, unit=nan, comment='freshly ground to taste')
Pandas(Index=109402, index=109402, 

Pandas(Index=167774, index=167774, input='1 tablespoon soaked chia seeds (1 teaspoon dry)', name='soaked chia seeds (1 teaspoon dry)', qty=1.0, range_end=0.0, unit='tablespoon', comment=nan)
Pandas(Index=167777, index=167777, input='1/8 to 1/4 teaspoon ground cinnamon (to taste)', name='ground cinnamon (to taste)', qty=0.5, range_end=0.0, unit='teaspoon', comment=nan)
Pandas(Index=167780, index=167780, input='2 to 3 tablespoons hot or boiling water (enough to just cover the oats)', name='hot or boiling water (enough to just cover the oats)', qty=2.0, range_end=0.0, unit='tablespoon', comment=nan)
Pandas(Index=167786, index=167786, input='1 tablespoon soaked chia seeds (1 teaspoon dry unsoaked; see note)', name='soaked chia seeds (1 teaspoon dry unsoaked; see note)', qty=1.0, range_end=0.0, unit='tablespoon', comment=nan)
Pandas(Index=167788, index=167788, input='2 to 3 tablespoons hot or boiling water (enough to just cover the oats)', name='hot or boiling water (enough to just cover th

In [23]:
salt_pepper = 0
for _, _, row in name_rows:
    if isinstance(row.name, str) and (row.name.lower().find('salt') > 0 or row.name.lower().find('pepper') > 0):
        salt_pepper += 1
        
salt_pepper

2999

In [24]:
salt_pepper = 0
for _, _, row in unit_rows:
    if isinstance(row.name, str) and (row.name.lower().find('salt') > 0 or row.name.lower().find('pepper') > 0):
        salt_pepper += 1
        
salt_pepper

62

In [25]:
salt_pepper = 0
for _, _, row in qty_rows:
    if isinstance(row.name, str) and (row.name.lower().find('salt') > 0 or row.name.lower().find('pepper') > 0):
        salt_pepper += 1
        
salt_pepper

10408

Problems:
- Jalapeno vs. Jalapenos
- `str.find` found a match that `re.search` didn't
- Mislabeled data
- `Salt and pepper` vs `salt and freshly ground pepper`

Solution:
- Make unplural if plural if can't be found
- Try `str.find` if `re.search` doesn't work
- Skip I guess